# Census Data Exploration Exercise

<b>Abridged Task Description</b>: Identify which Census tracts contain the highest concentrations of low-income and/or non-white populations in the United States for 2015. Feel free to take this a step further and provide additional data analyses that also apply to Vision Zero’s mission.

## Part 1: Census Data Exploration

### Step 1: Download Census Data

The exercise gave me hints about which tables I would need to use in order to download race and income data. I first navigated to [American Fact Finder](https://factfinder.census.gov/faces/nav/jsf/pages/index.xhtml), but I quickly saw that it would be too cumbersome to use to download data for all tracts in the United States. 

Instead, I found an [API Wrapper](https://github.com/datamade/census/blob/master/README.rst) for the Census's API. To use it, I found the variables of the tables I would need here:
- Non-white population data: https://api.census.gov/data/2015/acs/acs5/variables.html
- Low-income data: https://api.census.gov/data/2015/acs/acs5/subject/variables.html

After writing a script to download the data, I merged the data from both tables into a single dataframe. I also saved the data as a CSV file so I wouldn't have to re-download it each time I came back to my analyses.

In [1]:
# imports needed for the rest of the notebook included
import os

import folium
import geopandas as gpd
import numpy as np
import pandas as pd
from census import Census
from folium.plugins import FastMarkerCluster, HeatMap
from shapely.geometry import Point
from us import states

In [2]:
# Jupyter notebooks options
%matplotlib inline
pd.set_option("display.max_columns", None)

In [3]:
c = Census(os.environ.get("CENSUS_API_KEY"))

#### Poverty Data

In [4]:
poverty_data = [
    c.acs5subject.get(
        (
            "NAME",  # Tract Name
            "GEO_ID",  # Geography ID
            "S1701_C01_001E",  # Population for whom poverty status is determined
            "S1701_C01_042E",  # 200% or less of poverty level
        ),
        {"for": "tract:*", "in": "state:{}".format(state.fips)},
        year=2015,
    )
    for state in states.STATES
]

In [5]:
poverty_df = (
    pd.concat([pd.DataFrame(state_data) for state_data in poverty_data])
    .rename(
        columns={
            "S1701_C01_001E": "poverty_total_population",
            "S1701_C01_042E": "poverty_population_below_200%",
        },
    )
    .astype({"poverty_total_population": int, "poverty_population_below_200%": int})
)
poverty_df.to_csv("data/poverty.csv")

In [6]:
poverty_df.head()

NAME                GEO_ID  \
0  Census Tract 109.01, Madison County, Alabama  1400000US01089010901   
1  Census Tract 109.02, Madison County, Alabama  1400000US01089010902   
2  Census Tract 110.11, Madison County, Alabama  1400000US01089011011   
3  Census Tract 110.12, Madison County, Alabama  1400000US01089011012   
4  Census Tract 110.13, Madison County, Alabama  1400000US01089011013   

   poverty_total_population  poverty_population_below_200% state county  \
0                     13541                            557    01    089   
1                      2756                           1083    01    089   
2                      9696                            410    01    089   
3                      5848                            553    01    089   
4                      5177                           1051    01    089   

    tract  
0  010901  
1  010902  
2  011011  
3  011012  
4  011013

#### Population data

In [7]:
population_data = [
    c.acs5.get(
        (
            "NAME",  # Tract Name
            "GEO_ID",  # Geography ID
            "B01003_001E",  # Total estimated population
            "B02001_001E",  # Total population
            "B02001_003E",  # Black or African American alone
            "B02001_004E",  # American Indian and Alaska Native alone
            "B02001_005E",  # Asian alone
            "B02001_006E",  # Native Hawaiian and Other Pacific Islander alone
            "B02001_007E",  # Some other race alone
            "B02001_008E",  # Two or more races
        ),
        {"for": "tract:*", "in": "state:{}".format(state.fips)},
        year=2015,
    )
    for state in states.STATES
]

In [8]:
population_df = (
    pd.concat(pd.DataFrame(state_data) for state_data in population_data)
    .rename(
        columns={
            "B01003_001E": "total_estimated_population",
            "B02001_001E": "race_total_population",
            "B02001_003E": "Black_AA",
            "B02001_004E": "American_Indian_Alaskan_Native",
            "B02001_005E": "Asian",
            "B02001_006E": "Native_Hawaiian_Pacific_Islander",
            "B02001_007E": "other",
            "B02001_008E": "two_or_more",
        },
    )
    .astype({"total_estimated_population": int, "race_total_population": int})
)
population_df.to_csv("data/population.csv")

In [9]:
population_df.head()

NAME                GEO_ID  \
0  Census Tract 65.01, Mobile County, Alabama  1400000US01097006501   
1  Census Tract 65.02, Mobile County, Alabama  1400000US01097006502   
2     Census Tract 66, Mobile County, Alabama  1400000US01097006600   
3  Census Tract 67.01, Mobile County, Alabama  1400000US01097006701   
4  Census Tract 67.02, Mobile County, Alabama  1400000US01097006702   

   total_estimated_population  race_total_population  Black_AA  \
0                        5143                   5143     884.0   
1                       11578                  11578     451.0   
2                        5574                   5574     419.0   
3                        6436                   6436     883.0   
4                        3270                   3270     415.0   

   American_Indian_Alaskan_Native  Asian  Native_Hawaiian_Pacific_Islander  \
0                            31.0   13.0                               0.0   
1                             0.0  244.0                               0.0   
2                            12.0   96.0                               0.0   
3                            11.0  392.0                               0.0   
4                             0.0  416.0                               0.0   

   other  two_or_more state county   tract  
0    0.0        179.0    01    097  006501  
1   15.0        190.0    01    097  006502  
2   14.0          0.0    01    097  006600  
3  108.0        243.0    01    097  006701  
4    0.0        107.0    01    097  006702

#### Population and Poverty combined

In [10]:
poverty_and_race = poverty_df.merge(
    population_df, how="left", indicator=True
).set_index(["state", "county", "tract"])
poverty_and_race.to_csv("data/poverty_and_race.csv")
poverty_and_race.head()

NAME  \
state county tract                                                  
01    089    010901  Census Tract 109.01, Madison County, Alabama   
             010902  Census Tract 109.02, Madison County, Alabama   
             011011  Census Tract 110.11, Madison County, Alabama   
             011012  Census Tract 110.12, Madison County, Alabama   
             011013  Census Tract 110.13, Madison County, Alabama   

                                   GEO_ID  poverty_total_population  \
state county tract                                                    
01    089    010901  1400000US01089010901                     13541   
             010902  1400000US01089010902                      2756   
             011011  1400000US01089011011                      9696   
             011012  1400000US01089011012                      5848   
             011013  1400000US01089011013                      5177   

                     poverty_population_below_200%  \
state county tract                                   
01    089    010901                            557   
             010902                           1083   
             011011                            410   
             011012                            553   
             011013                           1051   

                     total_estimated_population  race_total_population  \
state county tract                                                       
01    089    010901                       13578                  13578   
             010902                        2756                   2756   
             011011                        9732                   9732   
             011012                        5848                   5848   
             011013                        5190                   5190   

                     Black_AA  American_Indian_Alaskan_Native  Asian  \
state county tract                                                     
01    089    010901     186.0                            55.0  109.0   
             010902     216.0                            33.0   35.0   
             011011     879.0                            16.0  653.0   
             011012     263.0                           135.0  213.0   
             011013     881.0                            15.0   87.0   

                     Native_Hawaiian_Pacific_Islander  other  two_or_more  \
state county tract                                                          
01    089    010901                               0.0   26.0        455.0   
             010902                               0.0   17.0         37.0   
             011011                              14.0   61.0        378.0   
             011012                               0.0    0.0        191.0   
             011013                               0.0    5.0        102.0   

                    _merge  
state county tract          
01    089    010901   both  
             010902   both  
             011011   both  
             011012   both  
             011013   both

I also thought it would be useful to download shapefiles for my analyses. I downloaded those here:
  - https://www.census.gov/geographies/mapping-files/time-series/geo/carto-boundary-file.2015.html

There wasn't a link providing access to tract shapefiles for all states in bulk, but I was able download them with this terminal command:

`wget -A "*tract*" -r ftp://ftp2.census.gov/geo/tiger/GENZ2015/shp`


### Step 2: Explore Data

Now that I had all of my data downloaded, it was time to start analyzing. 

First, I made copies of the dataframe I assembed above to summarize by county and state in case I would need them later. Then for each dataframe, I calculated the concentrations of people who were non-white and low-income.

- for non-white, I summed all of the racial categories and divided by the tract's population for whom race was determined.

- for low-income, I divided the number of people with an income below 200% of the poverty level by the tract's population for whom income was determined.

In [11]:
poverty_and_race_states = poverty_and_race.groupby("state").sum()
poverty_and_race_county = poverty_and_race.groupby(["state", "county"]).sum()

for df in [poverty_and_race, poverty_and_race_states, poverty_and_race_county]:
    df["race_nonwhite_ratio"] = (
        df.loc[:, "Black_AA":"two_or_more"].sum(axis=1) / df["race_total_population"]
    )
    df["poverty_ratio_below_200%"] = (
        df["poverty_population_below_200%"] / df["poverty_total_population"]
    )

I also made some maps at the state level for high level analysis

In [12]:
states_geojson = gpd.read_file("data/geographies/cb_2015_us_state_500k_simplified.json")

poverty_and_race_map = folium.Map(
    location=[39.833333, -98.583333], zoom_start=3, tiles="Stamen Toner"
)
folium.Choropleth(
    geo_data=states_geojson,
    name="% Nonwhite",
    data=poverty_and_race_states.reset_index()[["state", "race_nonwhite_ratio"]],
    columns=("state", "race_nonwhite_ratio"),
    key_on="feature.properties.GEOID",
    fill_color="YlOrRd",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Nonwhite ratio",
).add_to(poverty_and_race_map)

folium.Choropleth(
    geo_data=states_geojson,
    name="% Income >200% Poverty Level",
    data=poverty_and_race_states.reset_index()[["state", "poverty_ratio_below_200%"]],
    columns=("state", "poverty_ratio_below_200%"),
    key_on="feature.properties.GEOID",
    fill_color="BuPu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Low-income Ratio",
).add_to(poverty_and_race_map)

folium.LayerControl().add_to(poverty_and_race_map)
poverty_and_race_map

Now it was time to determine which tracts had high concentrations of nonwhite and low-income populations. The exercise worded it this way: 
`"concentrations of low-income and/or non-white populations"`

The _or_ of this piece of the exerciese was easy to deterimine. All I had to do was sort the dataframe by either my  low-income ratio or non-white ratio column.


#### Tracts with greatest non-white population concentrations:

There were 126 census tracts whose entire population was nonwhite:

In [13]:
poverty_and_race[poverty_and_race.race_nonwhite_ratio == 1].index.size

126

The first 20 of which were, sorted by total population:

In [14]:
poverty_and_race.sort_values(
    ["race_nonwhite_ratio", "race_total_population"], ascending=False
)[["NAME", "race_nonwhite_ratio", "race_total_population"]].head(20)

NAME  \
state county tract                                                       
17    031    252102        Census Tract 2521.02, Cook County, Illinois   
11    001    007703  Census Tract 77.03, District of Columbia, Dist...   
17    031    711200           Census Tract 7112, Cook County, Illinois   
11    001    009811  Census Tract 98.11, District of Columbia, Dist...   
22    071    001740      Census Tract 17.40, Orleans Parish, Louisiana   
17    031    530200           Census Tract 5302, Cook County, Illinois   
26    163    540300          Census Tract 5403, Wayne County, Michigan   
11    001    007707  Census Tract 77.07, District of Columbia, Dist...   
24    510    160500        Census Tract 1605, Baltimore city, Maryland   
13    121    007703         Census Tract 77.03, Fulton County, Georgia   
22    017    023500          Census Tract 235, Caddo Parish, Louisiana   
17    031    450300           Census Tract 4503, Cook County, Illinois   
47    157    005600          Census Tract 56, Shelby County, Tennessee   
01    073    005200         Census Tract 52, Jefferson County, Alabama   
26    163    500900          Census Tract 5009, Wayne County, Michigan   
22    051    027502   Census Tract 275.02, Jefferson Parish, Louisiana   
17    031    730600           Census Tract 7306, Cook County, Illinois   
22    079    012700        Census Tract 127, Rapides Parish, Louisiana   
17    031    400800           Census Tract 4008, Cook County, Illinois   
26    163    542600          Census Tract 5426, Wayne County, Michigan   

                     race_nonwhite_ratio  race_total_population  
state county tract                                               
17    031    252102                  1.0                   6358  
11    001    007703                  1.0                   5267  
17    031    711200                  1.0                   5021  
11    001    009811                  1.0                   5018  
22    071    001740                  1.0                   4681  
17    031    530200                  1.0                   4675  
26    163    540300                  1.0                   4591  
11    001    007707                  1.0                   4423  
24    510    160500                  1.0                   4318  
13    121    007703                  1.0                   4152  
22    017    023500                  1.0                   3895  
17    031    450300                  1.0                   3825  
47    157    005600                  1.0                   3735  
01    073    005200                  1.0                   3652  
26    163    500900                  1.0                   3365  
22    051    027502                  1.0                   3341  
17    031    730600                  1.0                   3276  
22    079    012700                  1.0                   3225  
17    031    400800                  1.0                   3164  
26    163    542600                  1.0                   3158

#### Tracts with greatest low-income population concentrations:

There were also 43 tracts with populations that had incomes below 200% the poverty level:

In [15]:
poverty_and_race[poverty_and_race["poverty_ratio_below_200%"] == 1].index.size

43

The first 20 of which were, sorted by total population:

In [16]:
poverty_and_race.sort_values(
    ["poverty_ratio_below_200%", "poverty_total_population"], ascending=False
)[["NAME", "poverty_ratio_below_200%", "poverty_total_population"]].head(20)

NAME  \
state county tract                                                       
12    086    980700      Census Tract 9807, Miami-Dade County, Florida   
13    051    000100            Census Tract 1, Chatham County, Georgia   
49    049    001602              Census Tract 16.02, Utah County, Utah   
25    025    980300   Census Tract 9803, Suffolk County, Massachusetts   
12    099    007100        Census Tract 71, Palm Beach County, Florida   
17    109    010500       Census Tract 105, McDonough County, Illinois   
36    081    042600          Census Tract 426, Queens County, New York   
37    135    011601  Census Tract 116.01, Orange County, North Caro...   
22    071    004402      Census Tract 44.02, Orleans Parish, Louisiana   
06    037    980014  Census Tract 9800.14, Los Angeles County, Cali...   
47    157    980100        Census Tract 9801, Shelby County, Tennessee   
13    121    003700            Census Tract 37, Fulton County, Georgia   
08    101    000903         Census Tract 9.03, Pueblo County, Colorado   
04    013    941100        Census Tract 9411, Maricopa County, Arizona   
17    087    980000        Census Tract 9800, Johnson County, Illinois   
06    053    980000     Census Tract 9800, Monterey County, California   
12    105    980000            Census Tract 9800, Polk County, Florida   
26    099    982200         Census Tract 9822, Macomb County, Michigan   
47    149    041500     Census Tract 415, Rutherford County, Tennessee   
12    086    008904     Census Tract 89.04, Miami-Dade County, Florida   

                     poverty_ratio_below_200%  poverty_total_population  
state county tract                                                       
12    086    980700                       1.0                      1011  
13    051    000100                       1.0                       902  
49    049    001602                       1.0                       382  
25    025    980300                       1.0                       224  
12    099    007100                       1.0                       195  
17    109    010500                       1.0                       141  
36    081    042600                       1.0                       134  
37    135    011601                       1.0                       100  
22    071    004402                       1.0                        81  
06    037    980014                       1.0                        70  
47    157    980100                       1.0                        64  
13    121    003700                       1.0                        54  
08    101    000903                       1.0                        52  
04    013    941100                       1.0                        43  
17    087    980000                       1.0                        42  
06    053    980000                       1.0                        39  
12    105    980000                       1.0                        30  
26    099    982200                       1.0                        28  
47    149    041500                       1.0                        25  
12    086    008904                       1.0                        19

With the _or_ question out of the way, it was time to tackle the _and_ portion. At first I thought of simply multiplying these two columns together to get a combined ratio, but that one number doesn’t tell you very much; It's impossible to tell which column, race or income, had more of an influence on the resulting "combined ratio".

Instead, I 'cut' each series of low-income and non-white concentrations into deciles and appended them back onto the dataframe. Then, I filtered the dataframe to show only tracts that were in the 10th decile for both categories.

#### Tracts with greatest low-income _and_ non-white population concentrations:

In [17]:
poverty_and_race["race_decile"] = pd.cut(
    poverty_and_race["race_nonwhite_ratio"], bins=10
)
poverty_and_race["poverty_decile"] = pd.cut(
    poverty_and_race["poverty_ratio_below_200%"], bins=10
)

non_white_low_income = poverty_and_race[
    (poverty_and_race["race_decile"] == pd.Interval(0.9, 1.0))
    & (poverty_and_race["poverty_decile"] == pd.Interval(0.9, 1.0))
]

columns = [
    "NAME",
    "poverty_population_below_200%",
    "race_nonwhite_ratio",
    "poverty_ratio_below_200%",
    "race_decile",
    "poverty_decile",
]

non_white_low_income[columns].sort_values(
    "poverty_population_below_200%", ascending=False
)

NAME  \
state county tract                                                       
39    035    108701        Census Tract 1087.01, Cuyahoga County, Ohio   
01    047    956400          Census Tract 9564, Dallas County, Alabama   
17    031    540102        Census Tract 5401.02, Cook County, Illinois   
26    021    002200          Census Tract 22, Berrien County, Michigan   
39    049    002900             Census Tract 29, Franklin County, Ohio   
48    201    331400            Census Tract 3314, Harris County, Texas   
01    097    004000            Census Tract 40, Mobile County, Alabama   
26    163    553400          Census Tract 5534, Wayne County, Michigan   
24    510    180100        Census Tract 1801, Baltimore city, Maryland   
39    035    109801        Census Tract 1098.01, Cuyahoga County, Ohio   
51    710    004100            Census Tract 41, Norfolk city, Virginia   
13    121    006802         Census Tract 68.02, Fulton County, Georgia   
39    049    001500             Census Tract 15, Franklin County, Ohio   
15    003    006202        Census Tract 62.02, Honolulu County, Hawaii   
39    061    008502          Census Tract 85.02, Hamilton County, Ohio   
37    107    010300    Census Tract 103, Lenoir County, North Carolina   
39    035    114300           Census Tract 1143, Cuyahoga County, Ohio   
             118602        Census Tract 1186.02, Cuyahoga County, Ohio   
27    123    033600         Census Tract 336, Ramsey County, Minnesota   
42    003    260900  Census Tract 2609, Allegheny County, Pennsylvania   
48    201    312800            Census Tract 3128, Harris County, Texas   
26    163    512200          Census Tract 5122, Wayne County, Michigan   
42    003    050900   Census Tract 509, Allegheny County, Pennsylvania   
39    061    003600             Census Tract 36, Hamilton County, Ohio   
51    710    004800            Census Tract 48, Norfolk city, Virginia   
18    089    030100             Census Tract 301, Lake County, Indiana   
36    047    080800           Census Tract 808, Kings County, New York   
01    097    000402          Census Tract 4.02, Mobile County, Alabama   
22    071    004800         Census Tract 48, Orleans Parish, Louisiana   
42    003    051100   Census Tract 511, Allegheny County, Pennsylvania   
11    001    006804  Census Tract 68.04, District of Columbia, Dist...   
22    071    004402      Census Tract 44.02, Orleans Parish, Louisiana   
13    121    003700            Census Tract 37, Fulton County, Georgia   
06    053    980000     Census Tract 9800, Monterey County, California   
      037    980004  Census Tract 9800.04, Los Angeles County, Cali...   
             980023  Census Tract 9800.23, Los Angeles County, Cali...   

                     poverty_population_below_200%  race_nonwhite_ratio  \
state county tract                                                        
39    035    108701                           4014             0.960435   
01    047    956400                           3128             0.952752   
17    031    540102                           2919             0.976744   
26    021    002200                           2758             0.901941   
39    049    002900                           2378             0.905411   
48    201    331400                           2234             0.994789   
01    097    004000                           2167             1.000000   
26    163    553400                           2114             0.991376   
24    510    180100                           1912             0.978703   
39    035    109801                           1869             1.000000   
51    710    004100                           1857             0.967397   
13    121    006802                           1802             1.000000   
39    049    001500                           1790             0.960905   
15    003    006202                           1742             0.991448   
39    061    008502                           1644   

## Part 2: Vision Zero

The exercise then asked me to "to take this a step further and provide additional data analyses that also apply to Vision Zero’s mission". With such a wide open problem, I had to pare it down into something a little more manageable.

I decided to preform a sort of thought experiment and take the part of the "governing body" of Vision Zero. Vision Zero is currently in a few major American [cities](https://visionzeronetwork.org/resources/vision-zero-cities/), but which city would be good to focus on next? I decided I'd use my analyses to help make an informed suggestion.

### Part 1: Collect and Prepare Vision Zero Data

I already had shapefiles of my areas of interest, so this time I needed to find data related to Vision Zero's work of preventing traffic fatalities. After searching online, I came across the [FARS](https://www.nhtsa.gov/research-data/fatality-analysis-reporting-system-fars) dataset -- pefect for this job. I downloaded the data for 2015 and proceded to load it into pandas along with the tract and county shapefiles. I then preformed a spatial merge to join the accidents' latitudes and longitudes with their appropriate state, county, and tract.

In [18]:
states_geography = gpd.read_file(
    "data/geographies/cb_2015_us_state_500k/cb_2015_us_state_500k.shp"
)

In [19]:
from pathlib import Path

pathlist = Path("data/geographies/tract_shapefiles").glob("**/*.shp")
tracts_geography = gpd.GeoDataFrame(
    pd.concat([gpd.read_file(str(path)) for path in pathlist], sort=False)
)

In [20]:
accidents = pd.read_csv(
    "data/FARS2015NationalCSV/accident.csv",
    dtype={"state": "object", "county": "object", "tract": "object"},
)

geometry = gpd.GeoSeries(
    [Point(xy) for xy in zip(accidents.LONGITUD, accidents.LATITUDE)]
)
accidents["geometry"] = geometry
accidents = gpd.GeoDataFrame(accidents)
accidents.head()

STATE  ST_CASE  VE_TOTAL  VE_FORMS  PVH_INVL  PEDS  PERNOTMVIT  PERMVIT  \
0      1    10001         1         1         0     0           0        1   
1      1    10002         1         1         0     0           0        1   
2      1    10003         1         1         0     0           0        2   
3      1    10004         1         1         0     0           0        1   
4      1    10005         2         2         0     0           0        2   

   PERSONS  COUNTY  CITY  DAY  MONTH  YEAR  DAY_WEEK  HOUR  MINUTE  NHS  \
0        1     127     0    1      1  2015         5     2      40    0   
1        1      83     0    1      1  2015         5    22      13    1   
2        2      11     0    1      1  2015         5     1      25    0   
3        1      45     0    4      1  2015         1     0      57    0   
4        2      45  2050    7      1  2015         4     7       9    0   

   RUR_URB  FUNC_SYS  RD_OWNER  ROUTE   TWAY_ID           TWAY_ID2  MILEPT  \
0        1         3         1      3      SR-5                NaN    1754   
1        1         1         1      1      I-65                NaN    3604   
2        1         3         1      2   US-SR 6                NaN    1958   
3        1         4         1      3     SR-27                NaN     566   
4        2         3         1      2  US-SR 53  HINTON WATERS AVE     308   

    LATITUDE  LONGITUD  SP_JUR  HARM_EV  MAN_COLL  RELJCT1  RELJCT2  TYP_INT  \
0  33.878653  -87.3253       0       35         0        0        1        1   
1  34.910442  -86.9087       0       34         0        0        1        1   
2  32.142006  -85.7585       0       42         0        0        1        1   
3  31.439814  -85.5103       0       53         0        0        1        1   
4  31.319331  -85.5151       0       12         6        0        2        3   

   WRK_ZONE  REL_ROAD  LGT_COND  WEATHER1  WEATHER2  WEATHER  SCH_BUS  \
0         0         4         2         1         0        1        0   
1         0         3         2        10         0       10        0   
2         0         4         2         1         0        1        0   
3         0         4         2        10         0       10        0   
4         0         1         1         1         0        1        0   

      RAIL  NOT_HOUR  NOT_MIN  ARR_HOUR  ARR_MIN  HOSP_HR  HOSP_MN  CF1  CF2  \
0  0000000        99       99         2       58       88       88    0    0   
1  0000000        99       99        22       20       88       88    0    0   
2  0000000        99       99         1       45       99       99    0    0   
3  0000000        99       99         1       15       88       88    0    0   
4  0000000        99       99         7       16       88       88    0    0   

   CF3  FATALS  DRUNK_DR                    geometry  
0    0       1         1  POINT (-87.32530 33.87865)  
1    0       1         0  POINT (-86.90870 34.91044)  
2    0       1         1  POINT (-85.75850 32.14201)  
3    0       1         1  POINT (-85.51030 31.43981)  
4    0       1         0  POINT (-85.51510 31.31933)

In [21]:
tracts_with_crashes = gpd.sjoin(accidents, tracts_geography, op="within")

In [22]:
tracts_with_crashes.head()

STATE  ST_CASE  VE_TOTAL  VE_FORMS  PVH_INVL  PEDS  PERNOTMVIT  PERMVIT  \
0        1    10001         1         1         0     0           0        1   
1        1    10002         1         1         0     0           0        1   
428      1    10430         1         1         0     0           0        3   
2        1    10003         1         1         0     0           0        2   
13       1    10014         1         1         0     0           0        1   

     PERSONS  COUNTY  CITY  DAY  MONTH  YEAR  DAY_WEEK  HOUR  MINUTE  NHS  \
0          1     127     0    1      1  2015         5     2      40    0   
1          1      83     0    1      1  2015         5    22      13    1   
428        3      83     0    6      8  2015         5    15      30    0   
2          2      11     0    1      1  2015         5     1      25    0   
13         1      11     0   11      1  2015         1     6      13    0   

     RUR_URB  FUNC_SYS  RD_OWNER  ROUTE             TWAY_ID TWAY_ID2  MILEPT  \
0          1         3         1      3                SR-5      NaN    1754   
1          1         1         1      1                I-65      NaN    3604   
428        1         6         2      4  CR-EASTER FERRY RD      NaN       0   
2          1         3         1      2             US-SR 6      NaN    1958   
13         1         4         1      2            US-SR 15      NaN    1454   

      LATITUDE  LONGITUD  SP_JUR  HARM_EV  MAN_COLL  RELJCT1  RELJCT2  \
0    33.878653  -87.3253       0       35         0        0        1   
1    34.910442  -86.9087       0       34         0        0        1   
428  34.909653  -87.0302       0        1         0        0        1   
2    32.142006  -85.7585       0       42         0        0        1   
13   32.162708  -85.7140       0        1         0        0        1   

     TYP_INT  WRK_ZONE  REL_ROAD  LGT_COND  WEATHER1  WEATHER2  WEATHER  \
0          1         0         4         2         1         0        1   
1          1         0         3         2        10         0       10   
428        1         0         4         1         2         0        2   
2          1         0         4         2         1         0        1   
13         1         0         4         1        10         0       10   

     SCH_BUS     RAIL  NOT_HOUR  NOT_MIN  ARR_HOUR  ARR_MIN  HOSP_HR  HOSP_MN  \
0          0  0000000        99       99         2       58       88       88   
1          0  0000000        99       99        22       20       88       88   
428        0  0000000        99       99        15       45       99       99   
2          0  0000000        99       99         1       45       99       99   
13         0  0000000        99       99         6       29       88       88   

     CF1  CF2  CF3  FATALS  DRUNK_DR                    geometry  index_right  \
0      0    0    0       1         1  POINT (-87.32530 33.87865)          367   
1      0    0    0       1         0  POINT (-86.90870 34.91044)          963   
428    0    0    0       1         0  POINT (-87.03020 34.90965)          963   
2      0    0    0       1         1  POINT (-85.75850 32.14201)          241   
13     0    0    0       1         1  POINT (-85.71400 32.16271)          241   

    STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID    NAME LSAD  \
0        01      127  020200  1400000US01127020200  01127020200     202   CT   
1        01      083  020202  1400000US01083020202  01083020202  202.02   CT   
428      01      083  020202  1400000US01083020202  01083020202  202.02   CT   
2        01      011  952200  1400000US01011952200  01011952200    9522   CT   
13       01      011  952200  1400000US01011952200  01011952200    9522   CT   

           ALAND     AWATER  
0     30020181.0   254512.0  
1    171352666.0   937318.0  
428  171352666.0   937318.0  
2    398494067.0  2087424.0  
13   398494067.0  2087424.0

As I was working with the data, I noticed something strange:

In [23]:
print(accidents.index.size)
print(tracts_with_crashes.index.size)

32538
32389


I was wondering why I lost some accidents after I merged dataframes. `gpd.sjoin()` uses "inner join" logic by default, so I specified `left_join` this time so I could see which tracts didn't make the cut.

In [24]:
tracts_with_crashes = gpd.sjoin(accidents, tracts_geography, how="left", op="within")

In [25]:
crashes_no_tract = tracts_with_crashes[pd.isna(tracts_with_crashes["index_right"])]
(crashes_no_tract.groupby(["LATITUDE", "LONGITUD"])["STATE"].count())

LATITUDE   LONGITUD 
21.355050  -158.1300      1
24.691761  -81.1950       1
27.878269  -82.5864       1
27.969039  -82.5737       1
29.297050  -94.8885       1
36.931119  -76.4069       1
36.996667  -76.4764       1
77.777700   777.7777     14
99.999900   999.9999    128
Name: STATE, dtype: int64

When I grouped by latitude and longitude, I noticed my issue. It looks like some of the crashes' exact locaitons were obfuscated in some way. But there were 7 that looked like valid latitude, longitude pairs. Why weren't they properly geocoded? I decided to plot them to find out.

In [26]:
no_tract_valid_lat_lon = crashes_no_tract.sort_values("LATITUDE")[
    ["LATITUDE", "LONGITUD", "geometry"]
].head(7)
no_tract_map = folium.Map(
    location=[39.833333, -98.583333], zoom_start=4, tiles="Stamen Toner"
)

points = folium.features.GeoJson(no_tract_valid_lat_lon.to_json())

no_tract_map.add_child(points)
no_tract_map

Turns out all of those crashes happened on bridges over water.

I then mapped all of the crashes as points:

In [27]:
accidents_map = folium.Map(
    location=[39.833333, -98.583333], zoom_start=4, tiles="Stamen Toner",
)
coords = [
    list(coord) for coord in zip(list(accidents.LATITUDE), list(accidents.LONGITUD))
]
accidents_map.add_child(FastMarkerCluster(coords))
accidents_map

And as a heatmap:

In [28]:
accidents_heatmap = folium.Map(
    location=[39.833333, -98.583333], tiles="Stamen Toner", zoom_start=4
)

a_hm = HeatMap(coords, min_opacity=0.4, radius=10, blur=15)

accidents_heatmap.add_child(a_hm)
accidents_heatmap

### Part 2: Analyze Vision Zero Data

I then started to analyze some of the data numerically. Because I was eventually going to consider the city level, first I wanted to find one state where I could focus my attention. To do this, I ranked the top 10 states by total number of crashes and crashes per capita.

In [29]:
# prepare table of crashes per state
crashes_per_state = tracts_with_crashes.groupby(["STATEFP"])["ST_CASE"].count()
crashes_per_state.index.names = ["state"]

poverty_race_crash_states = (
    poverty_and_race_states[
        [
            "poverty_ratio_below_200%",
            "race_nonwhite_ratio",
            "total_estimated_population",
        ]
    ]
    .join(crashes_per_state, how="left")
    .fillna(0)
)
poverty_race_crash_states["crashes_per_capita"] = (
    poverty_race_crash_states["ST_CASE"]
    / poverty_race_crash_states["total_estimated_population"]
)

In [30]:
top_10_crashes = (
    poverty_race_crash_states.sort_values("ST_CASE", ascending=False)
    .rank(ascending=False)
    .head(10)
    .reset_index()
)
top_10_crashes.state = top_10_crashes["state"].apply(lambda x: states.lookup(str(x)))

In [31]:
top_10_crashes_per_capita = (
    poverty_race_crash_states.sort_values("crashes_per_capita", ascending=False)
    .rank(ascending=False)
    .head(10)
    .reset_index()
)
top_10_crashes_per_capita.state = top_10_crashes_per_capita["state"].apply(
    lambda x: states.lookup(x)
)

#### Top ten states with the most fatal car accidents total

In [32]:
top_10_crashes[["state", "ST_CASE", "total_estimated_population"]]

state  ST_CASE  total_estimated_population
0           Texas      1.0                         2.0
1      California      2.0                         1.0
2         Florida      3.0                         4.0
3         Georgia      4.0                         8.0
4  North Carolina      5.0                        10.0
5            Ohio      6.0                         7.0
6        New York      7.0                         3.0
7        Illinois      8.0                         5.0
8  South Carolina      9.0                        24.0
9        Michigan     10.0                         9.0

#### Top ten states with the most fatal car accidents per capita

In [33]:
top_10_crashes_per_capita[["state", "crashes_per_capita", "total_estimated_population"]]

state  crashes_per_capita  total_estimated_population
0         Wyoming                 1.0                        51.0
1     Mississippi                 2.0                        31.0
2         Montana                 3.0                        44.0
3  South Carolina                 4.0                        24.0
4        Arkansas                 5.0                        32.0
5         Alabama                 6.0                        23.0
6        Kentucky                 7.0                        26.0
7    North Dakota                 8.0                        48.0
8        Oklahoma                 9.0                        28.0
9       Louisiana                10.0                        25.0

As one might expect, the total number of crashes rank is closely aligned with the rank of the total population i.e. states with more people, and hence more drivers, have more crashes. South Carolina was interesting though. It only ranks 24th in total population, but it had the 10th most traffic deaths. It was the 4th most in terms of fatal crashes per capita. This seems like it could be a good candidate for futher analysis.

In [34]:
south_carolina_crashes = tracts_with_crashes[(tracts_with_crashes.STATEFP == "45")]
coords = [
    list(coord)
    for coord in zip(
        list(south_carolina_crashes.LATITUDE), list(south_carolina_crashes.LONGITUD)
    )
]
sc_crash_heatmap = folium.Map(
    location=[33.9980, -81.0626], zoom_start=7, tiles="Stamen Toner"
)
hm_sc = HeatMap(coords, min_opacity=0.5, radius=10, blur=12,)

sc_crash_heatmap.add_child(hm_sc)
sc_crash_heatmap

After generating the heatmap, there were definitely a few hotspots around major cites and the Myrtle Beach area.

I was going to explore this map further by examining these statistics by county, but after looking at an overview of the counties overlaying the heatmap, I discovered that county lines may obfuscate the true nature of the dispersion of crashes. Fatal crashes seem to cluster around cities or major roadways and may be independent of county lines or even state lines -- a classic example of the [modifiable areal unit problem](https://en.wikipedia.org/wiki/Modifiable_areal_unit_problem). But considering other factors in addition to just the number of car accidents, I thought **Columbia** would be a logical choice to select as a good candidate for the next Vision Zero city. Not only is it South Carolina's second largest city, but its unique designation as the state's capital could help when it comes to drafting and adopting policy and well as being visible across the region. It has its fair share of crashes judging from the heat map, but these additiontal factors might also play an important part in pushing for adoption of Vision Zero policies and attitudes.

## Part 3: Next Steps

If I were to continue analyses with this topic, here are some more areas I would explore:
 - Find additional geographic boundaries (city limit or metro area boundaries especially) through which to explore the dispersion of fatal car accidents.
 - Identify additional data points to analyze along with simply counts of crashes. This could include further exploring the FARS dataset to break out subsets of intereset, including accidents that involved pedestrians or bicyclists, or downloading additional census data of interest.
 - This exercise stated at the beginning that "Studies have shown that low-income and/or non-white populations experience more traffic-related injuries and fatalities than other populations." I would be interested in exploring the presumption with the data collected for this exercise.